<h1> 8. Analysis 2 (BERTTopic) </h1>



In [1]:
#imports
import pandas as pd
import pickle   
from bertopic import BERTopic
import numpy as np
from bertopic import BERTopic
from sklearn.feature_extraction.text import CountVectorizer

bertopic versions
all C=15


1) bertopic 3 - model = BERTopic(calculate_probabilities=True, seed_topic_list=seed_topic_list)
2) bertopic 4 - model = BERTopic(seed_topic_list=seed_topic_list) - docs2
3) bertopic 5 - model = BERTopic(seed_topic_list=seed_topic_list) - docs2, n-gram, stop_words

<br>

4) bertopic_model_1: model = BERTopic(seed_topic_list=seed_topic_list) - docs, n-gram, stop_words
4) bertopic_model_2: model = BERTopic(seed_topic_list=seed_topic_list) - docs2, n-gram, stop_words

For each substance class, do removal of topics manually.

In [2]:
#seed words
ntp_words = ['time', 'period', 'periods', 'duration', 'clock', 'temporal', 'spacetime', 'timespan', 'timespans', 'timeline', 'timelines', 'elapse', 'elapsed', 'length', 'timewise', 'velocity', 'pace', 'rate', 'tempo', 'pass', 'passing', 'passed']
ftp_words = ['quick','quicker', 'quickly', 'quickest', 'fast', 'faster', 'fastest', 'fastened', 'rapid','rapidly', 'short', 'shorter', 'shortly', 'shortest','speedy', 'speedy','speeded', 'speedier', 'hurry', 'hurried', 'swift', 'swifter', 'swiftly', 'haste', 'hasty', 'brisk', 'turbo', 'accelerate', 'acceleration', 'accelerated', 'accelerating']
stp_words = ['slow', 'slower', 'slowly', 'slows', 'slowed', 'slowest', 'slowing', 'slowdown', 'long', 'looong', 'longer', 'longer', 'longest', 'steady', 'deceleration', 'decelerate', 'decelerating', 'decelerated', 'dilatory', 'dilation', 'infinity', 'eternity', 'lengthy', 'prolonged', 'protracted', 'extended', 'unending', 'endless']


seed_topic_list = [ntp_words, ftp_words, stp_words]

In [3]:
#data
docs = pd.read_pickle("BERTopic_docs_C=15.pkl")
df = pd.read_pickle("BERTopic_df_C=15.pkl")

#seed type
df["type"] = 0
for i, seed in enumerate(df.seed):
        if seed in ntp_words:
                df.loc[i, "type"] = "Neutral time perception words"
        elif seed in ftp_words:
                df.loc[i, "type"] = "Fast time perception words"
        elif seed in stp_words:
                df.loc[i, "type"] = "Slow time perception words"
        


#details dict2
details_dict = {}

for i, doc in enumerate(df.docs):
        details_dict[doc] = [df.loc[i, "seed"], df.loc[i, "type"], df.loc[i, "substance"], df.loc[i, "classes"], df.loc[i, "url"]]

In [ ]:
<h3> used to create docs2 </h3>

#removed theese in BERTopic3
fillerwords_nonesense_obscenity = [-1,0,3,4,7,38,54,62,117,143,149,187,188,199,226,232,233,263,283]
on_drugs = [8, 10,12,14,16,22,25,30,32,48,49,51,63,64,67,71,74,75,76,79,83,93,94,98,99,102,120,121,127,134,141,145,150,155,167,171,172,174,175,178,185,186,193,194,197,201,206,208,211,214,216,219,224,231,234,243,246,247,250,255,256,258,259,264,285]
administering_doses = [18,20,23,28,29,33,34,35,36,50,53,56,59,61,81,82,84,101,107,110,115,116,118,119,142,151,157,161,162,170,173,181,202,218,237,242,245,265,268,271,272,284]
police_illegality = [104,105,114,133,169,192,249]
remove_list = fillerwords_nonesense_obscenity + on_drugs + administering_doses + police_illegality
keep_list = [i for i in range(-1,286) if i not in remove_list]
#len remove_list = 133
#len keep_list = 154

#create docs2 for BERTopic4/5 
docs2 = []
for i, item in enumerate(df2.Document):
    if df2.loc[i, "Topic"] in keep_list:
        docs2.append(item)


with open("BERTopic_docs2_C=15", "wb") as f:
    pickle.dump(docs2, f)

In [4]:
vectorizer_model= CountVectorizer(stop_words="english") 

model = BERTopic(seed_topic_list=seed_topic_list, n_gram_range=(1,3), vectorizer_model=vectorizer_model)
topics, probs = model.fit_transform(docs)
model.save("bertopic_model_1")

In [33]:
model = BERTopic.load("bertopic3")

In [20]:
# Generate Labels
labels = model.generate_topic_labels(nr_words=2, topic_prefix=True, word_length=15, separator=" - ")
model.set_topic_labels(labels)


# change labels
#model.set_topic_labels({0:"Reinforcement Learning", 8:"Transformer Models"})

#topic_Info
topic_info = model.get_topic_info()

df2

In [7]:
df2

Document     ID  Topic
0      foreign substance that it was breaking down an...      0     -1
1      filter , and drink . i might want to down the ...      1     -1
2      likely i will repeat this by filling another c...      2    165
3      or addiction . i told her how stone from the a...      3    127
4      and a half of my friends weed cookies , and fe...      4     70
...                                                  ...    ...    ...
74099  , i had taken it on an empty stomach , which p...  74099     96
74100  growth . i did a lot of writing during the hig...  74100     88
74101  own . i smoke weed pretty regularly so i know ...  74101      7
74102  physically , but my mind was reeling over the ...  74102      3
74103  codeine is a nice little as for houdini by him...  74103    210

[74104 rows x 3 columns]

In [10]:
model

In [13]:
# Prepare your documents to be used in a dataframe
df2 = pd.DataFrame({"Document": docs, #replace with docs or docs2 variable depending on whether this is run 1 or 2
                          "ID": range(len(docs)), #replace with docs or docs2 variable depending on whether this is run 1 or 2
                          "Topic": model.topics_})

# Extract the top 50 representative documents per topics
repr_docs, _, _ = model._extract_representative_docs(c_tf_idf=model.c_tf_idf_,
                                                          documents=df,
                                                          topics=model.topic_representations_ ,
                                                          nr_repr_docs=50)


df2["Seed"] = 0
df2["Substance"] = 0
df2["Class"] = 0
df2["Url"] = 0


for i, doc in enumerate(df2.Document):
    df2.loc[i, "Seed"] = details_dict[doc][0]
    df2.loc[i, "Substance"] = details_dict[doc][2]
    df2.loc[i, "Class"] = details_dict[doc][3]
    df2.loc[i, "Url"] = details_dict[doc][4]


df2["Rank"] = 100000

#dataframe with scores for how representative each document is for the topic (lower rank - better)
for i, doc in enumerate(df2.Document):
    topic = df2.loc[i, "Topic"]
    if topic != -1 and doc in repr_docs[topic]:
        df2.loc[i, "Rank"] = repr_docs[topic].index(doc)
    


#sort by from lowest to highest
df2.sort_values(by=["Rank"], ascending=True, inplace=True)
df2.reset_index(drop=True, inplace=True)  


#create bolean True only for top 5 most represenative documents per substance per topic
df2["Include"] = False
combinations = []

for i, substance in enumerate(df2.Substance):
    combination = str(df2.loc[i, "Topic"]) + substance
    if combinations.count(combination) < 10:
        combinations.append(combination)
        df2.loc[i, "Include"] = True

KeyError: 'Topic'

In [ ]:
#for urls with no placeholders - find quote on the Erowid page
def prepare_url(s, url):
    s = s.replace(" .", ".").replace(" ,", ",").replace(" i ", " I ")
    words = s.split()  # split the string into a list of words
    first_three_words = ' '.join(words[:3])  # join the first three words with a space
    last_three_words = ' '.join(words[-3:])  # join the last three words with a space
    updated_url = url + "#:~:text=" + first_three_words.replace(" ", "%20") + "," + last_three_words.replace(" ", "%20")
    return (updated_url)

#create 
df4 = pd.DataFrame(columns=["Topic Nr", "Topic", "Substance", "Class", "Document"])


for i, item in enumerate(df2.Include):
    topic_nr = df2.loc[i, "Topic"]
    #get topic labels from topic_info df
    if  len(str(topic_nr)) == 1: 
        topic = "00" + topic_info.loc[topic_nr+1, "CustomName"]
    elif len(str(topic_nr)) == 2: 
        topic = "0" + topic_info.loc[topic_nr+1, "CustomName"]
    else:
        topic = topic_info.loc[topic_nr+1, "CustomName"]
    class_ = df2.loc[i, "Class"]
    substance = df2.loc[i, "Substance"]
    url = df2.loc[i, "Url"]
    doc = df2.loc[i, "Document"]
    #change url so it leads to the quote on the
    if any(substring in doc for substring in ["PERSON", "ORG", "GPE", "LOC"]):
        doc = "..." + doc + "... (NO URL)" 
    else:
        url = prepare_url(doc, url)    
        doc = "..." + doc + f"... (<a href={url}>URL</a>)"       

    df4.loc[len(df4.index)] = [topic_nr, topic, substance, class_, doc]


df4.to_csv("Representative Quotes Per Topic-Substance.csv")

In [ ]:
topic=15 #change here
substance="psilocybin mushrooms" #change here


def underline_word(sentence, word):
        return sentence.replace(word, "\x1B[4m" + word + "\x1B[0m")

for i, doc in enumerate(df2.Document):
    if df2.loc[i, "Topic"] == topic and df2.loc[i, "Substance"] == substance and df2.loc[i, "Include"]:
        doc = underline_word(doc, df2.loc[i, "Seed"])
        print(f"...{doc}...")
        print(df2.loc[i, "Url"])
        print()

In [ ]:
#find similar topics based of keyword(s)
similar_topics, similarity = model.find_topics("space", top_n=10)
print(similar_topics)

In [ ]:
#get 3 most representative docs per topic
topic=-1 #change topic here

list_of_3 = model.get_representative_docs(topic=topic)
for doc in list_of_3:
    print(doc)
    print("-----------")
    print(f"Seed: {details_dict[doc][0]}")
    print(f"Substance: {details_dict[doc][2]}")
    print(f"Class: {details_dict[doc][3]}")
    print(f"Url: {details_dict[doc][4]}")
    print("-----------")
    print()

In [ ]:
#visualize_documentsgraph
model.visualize_documents(docs2)

In [178]:
#get hierarhical documents
hierarchical_topics = model.hierarchical_topics(docs2)

100%|██████████| 132/132 [00:01<00:00, 108.33it/s]


In [ ]:
# Visualize these representations
model.visualize_hierarchy(hierarchical_topics=hierarchical_topics)

In [179]:
#topic tree
print(model.get_topic_tree(hierarchical_topics, max_distance=None, tight_layout=False))


.
├─date_infinity_time_universe_space
│    ├─infinity_eternity_infinite_universe_speed
│    │    ├─infinity_infinite_speed_fractal_slowing
│    │    │    ├─■──fractal_fractals_realities_infinity_existence ── Topic: 99
│    │    │    └─infinity_infinite_speed_slowing_slow
│    │    │         ├─■──infinity_speed_slowing_slow_infinite ── Topic: 10
│    │    │         └─■──infinity_infinite_eternity_universe_vastness ── Topic: 37
│    │    └─eternity_universe_hell_cycle_life
│    │         ├─universe_eternity_infinite_endless_creation
│    │         │    ├─■──universe_individuated_creation_eternity_consciousness ── Topic: 109
│    │         │    └─■──universe_eternity_try_endless_god ── Topic: 104
│    │         └─■──eternity_hell_torment_cycle_death ── Topic: 62
│    └─date_time_space_concept_exist
│         ├─time_space_concept_universe_existence
│         │    ├─■──space_universe_existence_existed_time ── Topic: 32
│         │    └─■──concept_time_exist_past_future ── Topic: 29
│       

<h3> remove these from visualization </h3>

In [ ]:
for item in keep_list:
    print(model.get_topic(item))
    print()

In [50]:
hierarchical_topics.to_csv("hierarchical topics.csv")



In [47]:
topics_list = [i for i in topics]
model.visualize_documents(docs=docs2, topics=topics_list,hide_annotations=False, hide_document_hover=False, custom_labels=True)

In [ ]:
#hierarchical documents and topics graph
model.visualize_hierarchical_documents(docs2, hierarchical_topics, hide_document_hover=False, custom_labels=True)


In [ ]:
#itnertopic distance map
model.visualize_topics(topics=[41,68,130,140,143,188,204,208,249,289,306])

In [ ]:
#bar charts
model.visualize_barchart(topics=XXX)

In [ ]:
#heat map
model.visualize_heatmap()

<h3> Class topic modelling </h3>

In [210]:
#get substance classes labels for each doc
substances = []
for item in docs2:
    substances.append(details_dict[item][1])



#topics per class - https://maartengr.github.io/BERTopic/getting_started/topicsperclass/topicsperclass.html
df3 = model.topics_per_class(docs2, classes=substances)


#get frequency of substance class/documents of that class
freq_dict = dict(df.type.value_counts())


#the series 'class' is not about substance classes but has substances in it. The term class comes from the BerTopic documentation.
for i, item in enumerate(df3.Frequency):
    df3.loc[i, "Frequency"] = df3.loc[i, "Frequency"]/freq_dict[df3.loc[i, "Class"]]
    

In [ ]:
infinity_fear_ego_fractal_eternity (621) - 57,158,185,242,248
music_placeholder_trip_clock_song (507) - 12,21,66,1
fear_ego_death_terror_eternity (585) - 41,68,130,140,143,188,204,208,249,289,306
ceiling_clouds_walls_black_spiders (595) - 49,76,121,124,138,148,190,199,209,210,216,221,230,239,271,274,294


model.visualize_topics_per_class(df3, topics=[280, 153], normalize_frequency=True)

In [ ]:
#create Erowid qutoes (ignore)
dictx = {}
for i, item in enumerate(df.classes):
    substance = df.loc[i, "substance"]
    if item not in dictx:
        dictx[item] = []
    if substance not in dictx[item]:
        dictx[item].append(substance)


listx = []
for i, item in enumerate(topic_info.CustomName):
    if int(topic_info.loc[i, "Topic"]) not in remove_list:
        listx.append(item)


#for substances
for item in dictx.values():
    for i in item:
        print(f"<option value='{i}'>{i}</option>")

#for substances
for i in dictx.keys():
    print(f"<option value='{i}'>{i}</option>")